<a href="https://colab.research.google.com/github/the-fur-lover-sketch/effective-invention/blob/main/Music_player0921.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
# -*- coding: utf-8 -*-
import requests
import re
import numpy as np
from scipy import signal
from scipy.io.wavfile import write
from IPython.display import Audio, display

# ---------- 設定 ----------
SHEET_URL = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
SR = 44100              # サンプリングレート
AMPLITUDE = 0.9         # 正規化前の振幅（後で正規化するので大きめで可）
CLAMP_TO_NEXT = True    # True: 音が次の開始に被る場合は切り詰める（デフォルト）
FADE_MS = 8             # クリック防止のフェード長（ミリ秒）

# ---------- ユーティリティ ----------
def split_top_level_commas(s):
    """括弧/角括弧の深さを見てトップレベルのカンマだけで分割する"""
    parts = []
    cur = []
    depth = 0
    i = 0
    while i < len(s):
        ch = s[i]
        if ch in '[({':
            depth += 1
            cur.append(ch)
        elif ch in '])}':
            depth -= 1
            cur.append(ch)
        elif ch == ',' and depth == 0:
            parts.append(''.join(cur).strip())
            cur = []
        else:
            cur.append(ch)
        i += 1
    if cur:
        parts.append(''.join(cur).strip())
    return parts

def make_wave_for_freq(freq, length_samples, waveform='sine'):
    """周波数1つ分の波形（指定サンプル長）を返す"""
    if length_samples <= 0:
        return np.zeros(0, dtype=np.float32)
    t = np.arange(length_samples) / SR
    if freq == 0:
        return np.zeros_like(t, dtype=np.float32)
    if waveform.startswith('sine'):
        return np.sin(2*np.pi*freq*t)
    elif waveform.startswith('square'):
        return signal.square(2*np.pi*freq*t)
    elif waveform.startswith('saw'):
        return signal.sawtooth(2*np.pi*freq*t)
    elif waveform.startswith('triangle'):
        return signal.sawtooth(2*np.pi*freq*t, 0.5)
    else:
        return np.sin(2*np.pi*freq*t)

def apply_fade(wave, fade_ms=FADE_MS):
    """線形のフェードイン/アウトを追加（サンプル長を超えないように調整）"""
    n = len(wave)
    if n == 0:
        return wave
    fade_samples = int(round(min(fade_ms/1000.0 * SR, n//2)))
    if fade_samples <= 0:
        return wave
    # in
    in_env = np.linspace(0.0, 1.0, fade_samples, endpoint=False)
    wave[:fade_samples] *= in_env
    # out
    out_env = np.linspace(1.0, 0.0, fade_samples, endpoint=False)
    wave[-fade_samples:] *= out_env
    return wave

# ---------- スコア読み込み & 前処理 ----------
resp = requests.get(SHEET_URL)
code = resp.text.splitlines()

# 変数定義だけ eval/exec（t_1, f_1, ds_1, di_1, sp_1 等）
var_lines = [ln for ln in code if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', ln)]
# 実行して変数をグローバルに定義
exec('\n'.join(var_lines), globals())

# スコア行抽出（t_n*... で始まる行）
score_raw = [ln.strip() for ln in code if re.match(r'^\s*t_\d+\s*\*', ln)]

score = []      # (start(float), [freqs], duration(float), waveform(str))
prev = {}       # index -> 評価済み値（start,freq,duration,wave）

for idx, line in enumerate(score_raw):
    parts = split_top_level_commas(line)
    fixed = []
    for i, part in enumerate(parts):
        p = part.strip()
        # '.' の継承（ドットが単独で出てくる形式を想定）
        if p == '.':
            val = prev.get(i)
        else:
            # 評価（式、数値、リスト、文字列など）
            # eval を使うが変数は既に globals() に入っている
            try:
                val = eval(p, globals())
            except Exception as e:
                # 評価できない場合は None にして通知
                print(f"[WARN] eval error line {idx+1}, col {i+1}: '{p}' -> {e}")
                val = None
        # 周波数列（列 index 1）は常にリストに統一
        if i == 1:
            if isinstance(val, (int, float)):
                val = [float(val)]
            elif isinstance(val, (list, tuple)):
                # すべて float に
                val = [float(x) for x in val]
            else:
                # 空リストで扱う（安全処理）
                val = []
        # 波形列（index 3）は文字列化しておく
        if i == 3 and isinstance(val, str):
            # remove surrounding quotes if any (eval typically returns proper str)
            val = val.strip()
        fixed.append(val)
        prev[i] = val
    # 最低限 start と freq と duration は存在している前提
    start = float(fixed[0]) if fixed[0] is not None else 0.0
    freqs = fixed[1] if len(fixed) > 1 else []
    duration = float(fixed[2]) if len(fixed) > 2 and fixed[2] is not None else 0.0
    waveform = fixed[3] if len(fixed) > 3 and fixed[3] is not None else 'sine'
    score.append((start, freqs, duration, waveform))

# ---------- ノートを配置する（タイムライン方式） ----------
# まず各ノートの「実際に鳴らす duration（秒）」を決める（必要に応じクランプ）
processed_notes = []  # list of (start, freqs, used_duration, waveform)
n = len(score)
for i, (start, freqs, duration, waveform) in enumerate(score):
    used_duration = float(duration)
    if CLAMP_TO_NEXT and i < n-1:
        next_start = float(score[i+1][0])
        max_allowed = next_start - start
        # 負にならないように
        if max_allowed < 0:
            max_allowed = 0
        # 小数点誤差対策の微小値を引く（隙間を少し残す）
        epsilon = 1.0 / SR
        if used_duration > max_allowed:
            used_duration = max(0.0, max_allowed - epsilon)
    processed_notes.append((float(start), list(freqs), float(used_duration), waveform))

# 全体長を決める
end_time = 0.0
for start, freqs, used_duration, waveform in processed_notes:
    end_time = max(end_time, start + used_duration)
total_samples = int(np.ceil(end_time * SR)) if end_time > 0 else 1
timeline = np.zeros(total_samples, dtype=np.float32)

# 各ノートをタイムラインに追加
for start, freqs, used_duration, waveform in processed_notes:
    if used_duration <= 0 or len(freqs) == 0:
        continue
    note_samples = int(round(used_duration * SR))
    if note_samples <= 0:
        continue
    # 各周波数の波を作って合成
    waves = [make_wave_for_freq(f, note_samples, waveform) for f in freqs]
    note_wave = np.sum(waves, axis=0) / max(1, len(waves))  # 平均化
    # フェードを入れてクリックを防ぐ
    note_wave = apply_fade(note_wave, FADE_MS)
    # 振幅スケール
    note_wave = note_wave * AMPLITUDE
    # 挿入位置
    idx0 = int(round(start * SR))
    idx1 = idx0 + note_samples
    # timeline に加算（範囲をチェック）
    if idx0 >= total_samples:
        # 開始が全体長を超える場合は拡張（稀）
        extra = idx0 + note_samples - total_samples
        timeline = np.concatenate([timeline, np.zeros(extra, dtype=np.float32)])
        total_samples = len(timeline)
    if idx1 > len(timeline):
        # 範囲超過なら末尾に拡張
        extra = idx1 - len(timeline)
        timeline = np.concatenate([timeline, np.zeros(extra, dtype=np.float32)])
    timeline[idx0:idx1] += note_wave

# 正規化（安全に）
peak = np.max(np.abs(timeline)) if timeline.size > 0 else 1.0
if peak > 0:
    timeline = timeline / peak * 0.95  # 0.95 で頭打ち

# WAV に書き出す（16bit）
out_fname = "timeline_output.wav"
timeline_int16 = np.int16(timeline * 32767)
write(out_fname, SR, timeline_int16)

# Notebook 再生と完了表示
print(f"WAV written: {out_fname}")
display(Audio(out_fname, rate=SR, autoplay=False))

from google.colab import files

files.download("timeline_output.wav")





WAV written: timeline_output.wav


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [3]:

from IPython.display import Audio, display


import requests
import re
import numpy as np
from scipy.io.wavfile import write

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
var_lines = [line for line in code.splitlines()
             if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

# ===== Preprocessing: Fix '.' and unify single/ chord frequencies =====
prev = {}
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    # トップレベルカンマのみで分割（リスト内カンマは無視）
    parts = re.split(r',\s*(?![^\[]*\])', line)
    fixed_parts = []
    for i, p in enumerate(parts):
        p_clean = p.replace("\n","").replace("\r","").strip()
        if p_clean == '.':
            val = prev.get(i)
        else:
            try:
                val = eval(p_clean)
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p_clean}")
                print("Exception:", e)
                val = None

        # 単音をリストに統一
        if i == 1:  # freq 列
            if isinstance(val, int) or isinstance(val, float):
                val = [val]
            elif isinstance(val, list):
                pass
            else:
                val = []
        fixed_parts.append(val)
        prev[i] = val
    score_lines_fixed.append(fixed_parts)

print("=== FIXED SCORE LINES (ALL, freq unified) ===")
for idx, line in enumerate(score_lines_fixed, start=1):
    print(f"{idx:02d}: {line}")
print(f"\nTotal lines processed: {len(score_lines_fixed)}\n")

# ===== WAV Generation Parameters =====
sample_rate = 44100  # 44.1 kHz
amplitude = 0.2      # 音量調整

def generate_wave(freq_list, duration, waveform='square', sample_rate=44100):
    t = np.linspace(0, duration, int(sample_rate * duration), endpoint=False)
    wave = np.zeros_like(t)
    for f in freq_list:
        if waveform == 'square':
            wave += amplitude * np.sign(np.sin(2 * np.pi * f * t))
        elif waveform == 'sine':
            wave += amplitude * np.sin(2 * np.pi * f * t)
    wave /= max(1, len(freq_list))  # 和音の音量調整
    return wave

# ===== Generate full audio =====
full_wave = np.array([], dtype=np.float32)

for line in score_lines_fixed:
    start_time, freq_list, duration, waveform = line
    wave = generate_wave(freq_list, duration, waveform, sample_rate)
    full_wave = np.concatenate([full_wave, wave])

# ===== Normalize & Convert to 16-bit PCM =====
full_wave_int16 = np.int16(full_wave / np.max(np.abs(full_wave)) * 32767)

# ===== Save to WAV =====
output_file = "output.wav"
write(output_file, sample_rate, full_wave_int16)
print(f"WAV file generated: {output_file}")


# ===== Display audio player in notebook =====
display(Audio(output_file, autoplay=False))


=== FIXED SCORE LINES (ALL, freq unified) ===
01: [5.0, [220], 0.15, 'square']
02: [7.5, [220], 0.15, 'square']
03: [10.5, [220], 0.15, 'square']
04: [11.0, [440], 0.15, 'square']
05: [11.5, [220], 0.15, 'square']
06: [12.0, [220], 0.15, 'square']
07: [12.5, [440], 0.15, 'square']
08: [13.0, [220], 0.15, 'square']
09: [13.5, [440], 0.15, 'square']
10: [14.0, [440], 0.15, 'square']
11: [14.5, [220], 0.15, 'square']
12: [15.0, [220], 0.15, 'square']
13: [15.5, [440], 0.15, 'square']
14: [16.0, [220], 0.15, 'square']
15: [16.5, [440], 0.15, 'square']
16: [17.0, [220], 0.15, 'square']
17: [17.5, [220], 0.15, 'square']
18: [18.0, [440], 0.15, 'square']
19: [18.5, [220], 0.15, 'square']
20: [19.0, [440], 0.15, 'square']
21: [19.5, [220], 0.15, 'square']
22: [20.0, [220], 0.15, 'square']
23: [20.5, [440], 0.15, 'square']
24: [21.0, [220], 0.15, 'square']
25: [21.5, [440], 0.15, 'square']
26: [22.0, [440], 0.15, 'square']
27: [22.5, [220], 0.15, 'square']
28: [23.0, [220], 0.15, 'square']
29: 

In [ ]:
import requests
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
var_lines = [line for line in code.splitlines()
             if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

# ===== Debug: Fix '.' and unify single/ chord frequencies =====
prev = {}
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    # トップレベルカンマのみで分割（リスト内カンマは無視）
    parts = re.split(r',\s*(?![^\[]*\])', line)
    fixed_parts = []
    for i, p in enumerate(parts):
        p_clean = p.replace("\n","").replace("\r","").strip()
        if p_clean == '.':
            val = prev.get(i)
        else:
            try:
                val = eval(p_clean)
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p_clean}")
                print("Exception:", e)
                val = None

        # ===== 単音をリストに統一 =====
        if i == 1:  # freq 列
            if isinstance(val, int) or isinstance(val, float):
                val = [val]
            elif isinstance(val, list):
                pass
            else:
                val = []
        fixed_parts.append(val)
        prev[i] = val
    score_lines_fixed.append(fixed_parts)

# ===== デバッグ表示: 全行表示 =====
print("=== FIXED SCORE LINES (ALL, freq unified) ===")
for idx, line in enumerate(score_lines_fixed, start=1):
    print(f"{idx:02d}: {line}")

print(f"\nTotal lines processed: {len(score_lines_fixed)}")


=== FIXED SCORE LINES (ALL, freq unified) ===
01: [0.125, [220], 0.0875, 'square']
02: [0.25, [440], 0.0875, 'square']
03: [0.375, [220], 0.0875, 'square']
04: [0.5, [220], 0.0875, 'square']
05: [0.625, [440], 0.0875, 'square']
06: [0.75, [220], 0.0875, 'square']
07: [0.875, [440], 0.0875, 'square']
08: [1.0, [440], 0.0875, 'square']
09: [1.125, [220], 0.0875, 'square']
10: [1.25, [220], 0.0875, 'square']
11: [1.375, [440], 0.0875, 'square']
12: [1.5, [220], 0.0875, 'square']
13: [1.625, [440], 0.0875, 'square']
14: [1.75, [220], 0.0875, 'square']
15: [1.875, [220], 0.0875, 'square']
16: [2.0, [440], 0.0875, 'square']
17: [2.125, [220], 0.0875, 'square']
18: [2.25, [440], 0.0875, 'square']
19: [2.375, [220], 0.0875, 'square']
20: [2.5, [220], 0.0875, 'square']
21: [2.625, [440], 0.0875, 'square']
22: [2.75, [220], 0.0875, 'square']
23: [2.875, [440], 0.0875, 'square']
24: [3.0, [440], 0.0875, 'square']
25: [3.125, [220], 0.0875, 'square']
26: [3.25, [220], 0.0875, 'square']
27: [3.375,

In [ ]:
import requests
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
var_lines = [line for line in code.splitlines()
             if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

# ===== Debug: Fix '.' by replacing with previous values (top-level comma only) =====
prev = {}
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    # トップレベルカンマのみで分割（リスト内カンマは無視）
    parts = re.split(r',\s*(?![^\[]*\])', line)
    fixed_parts = []
    for i, p in enumerate(parts):
        p_clean = p.replace("\n","").replace("\r","").strip()
        if p_clean == '.':
            fixed_parts.append(prev.get(i))
        else:
            try:
                val = eval(p_clean)
                fixed_parts.append(val)
                prev[i] = val
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p_clean}")
                print("Exception:", e)
                fixed_parts.append(None)
    score_lines_fixed.append(fixed_parts)

# ===== デバッグ表示: 全行表示 =====
print("=== FIXED SCORE LINES (ALL) ===")
for idx, line in enumerate(score_lines_fixed, start=1):
    print(f"{idx:02d}: {line}")

print(f"\nTotal lines processed: {len(score_lines_fixed)}")


=== FIXED SCORE LINES (ALL) ===
01: [0.125, 220, 0.0875, 'square']
02: [0.25, 440, 0.0875, 'square']
03: [0.375, 220, 0.0875, 'square']
04: [0.5, 220, 0.0875, 'square']
05: [0.625, 440, 0.0875, 'square']
06: [0.75, 220, 0.0875, 'square']
07: [0.875, 440, 0.0875, 'square']
08: [1.0, 440, 0.0875, 'square']
09: [1.125, 220, 0.0875, 'square']
10: [1.25, 220, 0.0875, 'square']
11: [1.375, 440, 0.0875, 'square']
12: [1.5, 220, 0.0875, 'square']
13: [1.625, 440, 0.0875, 'square']
14: [1.75, 220, 0.0875, 'square']
15: [1.875, 220, 0.0875, 'square']
16: [2.0, 440, 0.0875, 'square']
17: [2.125, 220, 0.0875, 'square']
18: [2.25, 440, 0.0875, 'square']
19: [2.375, 220, 0.0875, 'square']
20: [2.5, 220, 0.0875, 'square']
21: [2.625, 440, 0.0875, 'square']
22: [2.75, 220, 0.0875, 'square']
23: [2.875, 440, 0.0875, 'square']
24: [3.0, 440, 0.0875, 'square']
25: [3.125, 220, 0.0875, 'square']
26: [3.25, 220, 0.0875, 'square']
27: [3.375, 440, 0.0875, 'square']
28: [3.5, 220, 0.0875, 'square']
29: [3.62

In [ ]:
import requests
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
var_lines = [line for line in code.splitlines() if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

# ===== Debug: Fix '.' by replacing with previous values (top-level comma only) =====
prev = {}
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    # トップレベルカンマのみで分割
    # [ の中にあるカンマは無視
    parts = re.split(r',\s*(?![^\[]*\])', line)
    fixed_parts = []
    for i, p in enumerate(parts):
        p_clean = p.replace("\n","").replace("\r","").strip()
        if p_clean == '.':
            fixed_parts.append(prev.get(i))
        else:
            try:
                val = eval(p_clean)
                fixed_parts.append(val)
                prev[i] = val
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p_clean}")
                print("Exception:", e)
                fixed_parts.append(None)
    score_lines_fixed.append(fixed_parts)

# ===== デバッグ表示 =====
print("=== FIXED SCORE LINES (first 20) ===")
for line in score_lines_fixed[:20]:
    print(line)

print(f"\nTotal lines processed: {len(score_lines_fixed)}")


=== FIXED SCORE LINES (first 20) ===
[0.125, 220, 0.0875, 'square']
[0.25, 440, 0.0875, 'square']
[0.375, 220, 0.0875, 'square']
[0.5, 220, 0.0875, 'square']
[0.625, 440, 0.0875, 'square']
[0.75, 220, 0.0875, 'square']
[0.875, 440, 0.0875, 'square']
[1.0, 440, 0.0875, 'square']
[1.125, 220, 0.0875, 'square']
[1.25, 220, 0.0875, 'square']
[1.375, 440, 0.0875, 'square']
[1.5, 220, 0.0875, 'square']
[1.625, 440, 0.0875, 'square']
[1.75, 220, 0.0875, 'square']
[1.875, 220, 0.0875, 'square']
[2.0, 440, 0.0875, 'square']
[2.125, 220, 0.0875, 'square']
[2.25, 440, 0.0875, 'square']
[2.375, 220, 0.0875, 'square']
[2.5, 220, 0.0875, 'square']

Total lines processed: 64


In [ ]:
import requests
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
var_lines = [line for line in code.splitlines() if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

print("=== RAW SCORE LINES (first 10) ===")
for line in score_lines_raw[:10]:
    print(line)

# ===== Debug: Fix '.' by replacing with previous values =====
prev = {}  # 前の値を保持
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    # トップレベルカンマのみで分割（リスト内カンマは無視）
    parts = re.split(r',\s*(?![^\[]*\])', line)
    fixed_parts = []
    for i, p in enumerate(parts):
        p_clean = p.replace("\n","").replace("\r","").strip()
        if p_clean == '.':
            fixed_parts.append(prev.get(i))
        else:
            try:
                val = eval(p_clean)
                fixed_parts.append(val)
                prev[i] = val
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p_clean}")
                print("Exception:", e)
                fixed_parts.append(None)
    score_lines_fixed.append(fixed_parts)

print("\n=== FIXED SCORE LINES (first 10) ===")
for line in score_lines_fixed[:10]:
    print(line)

print(f"\nTotal lines processed: {len(score_lines_fixed)}")


=== RAW SCORE LINES (first 10) ===
t_1*1  + sp_1 , f_1*1           , ds_1*t_1 + di_1 , "square"
t_1*2  + sp_1 , f_1*2           , .                , .
t_1*3  + sp_1 , f_1*1           , .                , .
t_1*4  + sp_1 , f_1*1           , .                , .
t_1*5  + sp_1 , f_1*2           , .                , .
t_1*6  + sp_1 , f_1*1           , .                , .
t_1*7  + sp_1 , f_1*2           , .                , .
t_1*8  + sp_1 , f_1*2           , .                , .
t_1*9  + sp_1 , f_1*1           , .                , .
t_1*10 + sp_1 , f_1*1           , .                , .

=== FIXED SCORE LINES (first 10) ===
[0.125, 220, 0.0875, 'square']
[0.25, 440, 0.0875, 'square']
[0.375, 220, 0.0875, 'square']
[0.5, 220, 0.0875, 'square']
[0.625, 440, 0.0875, 'square']
[0.75, 220, 0.0875, 'square']
[0.875, 440, 0.0875, 'square']
[1.0, 440, 0.0875, 'square']
[1.125, 220, 0.0875, 'square']
[1.25, 220, 0.0875, 'square']

Total lines processed: 64


In [ ]:
import requests
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

print("=== RAW SCORE LINES (first 10) ===")
for line in score_lines_raw[:10]:
    print(line)

# ===== Debug: Fix '.' by replacing with previous values =====
prev = {}  # 前の値を保持
score_lines_fixed = []

for idx, line in enumerate(score_lines_raw):
    parts = [p.strip() for p in line.split(",")]
    fixed_parts = []
    for i, p in enumerate(parts):
        if p == '.':
            fixed_parts.append(prev.get(i))
        else:
            try:
                val = eval(p.replace("\n","").replace("\r","").strip())
                fixed_parts.append(val)
                prev[i] = val
            except Exception as e:
                print(f"[ERROR] Line {idx+1}, column {i+1}: {p}")
                print("Exception:", e)
                fixed_parts.append(None)
    score_lines_fixed.append(fixed_parts)

print("\n=== FIXED SCORE LINES (first 10) ===")
for line in score_lines_fixed[:10]:
    print(line)

print(f"\nTotal lines processed: {len(score_lines_fixed)}")


=== RAW SCORE LINES (first 10) ===
t_1*1  + sp_1 , f_1*1           , ds_1*t_1 + di_1 , "square"
t_1*2  + sp_1 , f_1*2           , .                , .
t_1*3  + sp_1 , f_1*1           , .                , .
t_1*4  + sp_1 , f_1*1           , .                , .
t_1*5  + sp_1 , f_1*2           , .                , .
t_1*6  + sp_1 , f_1*1           , .                , .
t_1*7  + sp_1 , f_1*2           , .                , .
t_1*8  + sp_1 , f_1*2           , .                , .
t_1*9  + sp_1 , f_1*1           , .                , .
t_1*10 + sp_1 , f_1*1           , .                , .
[ERROR] Line 49, column 2: [f_1*1
Exception: '[' was never closed (<string>, line 1)
[ERROR] Line 49, column 3: f_1*4]
Exception: unmatched ']' (<string>, line 1)
[ERROR] Line 50, column 2: [f_1*2
Exception: '[' was never closed (<string>, line 1)
[ERROR] Line 50, column 3: f_1*4]
Exception: unmatched ']' (<string>, line 1)
[ERROR] Line 51, column 2: [f_1*1
Exception: '[' was never closed (<string>, line 1

In [ ]:
import numpy as np
import requests
from scipy.io.wavfile import write
from IPython.display import Audio
import re

# ===== Load Code =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Only Variable Definitions =====
# 代入文のみを抽出して実行
var_lines = [line for line in code.splitlines() if re.match(r'^\s*(t_|f_|ds_|di_|sp_)\d*\s*=', line)]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines()
                   if re.match(r'^\s*t_\d+\s*\*', line)]

# ===== Fix '.' by replacing with previous values =====
prev = {}  # 前の値を保持
score_lines_fixed = []

for line in score_lines_raw:
    parts = [p.strip() for p in line.split(",")]
    fixed_parts = []
    for i, p in enumerate(parts):
        if p == '.':
            fixed_parts.append(prev.get(i))
        else:
            val = eval(p)
            fixed_parts.append(val)
            prev[i] = val
    score_lines_fixed.append(fixed_parts)

# ===== WAV Generation =====
fs = 44100

def generate_wave(frequency, duration, wave_type="square"):
    t = np.linspace(0, duration, int(fs*duration), endpoint=False)
    if wave_type == "square":
        return np.sign(np.sin(2*np.pi*frequency*t))
    elif wave_type == "sine":
        return np.sin(2*np.pi*frequency*t)
    elif wave_type == "triangle":
        return 2*np.abs(2*((t*frequency)%1)-1)-1
    elif wave_type == "sawtooth":
        return 2*((t*frequency)%1)-1
    else:
        return np.zeros_like(t)

full_wave = np.array([], dtype=np.float32)

for t_val, f_val, dur_val, wave_val in score_lines_fixed:
    duration = dur_val or t_1
    wave_type = wave_val or "square"
    if isinstance(f_val, list):
        wave = sum(generate_wave(f, duration, wave_type) for f in f_val)
        wave /= len(f_val)
    else:
        wave = generate_wave(f_val, duration, wave_type)
    full_wave = np.concatenate((full_wave, wave))

# ===== Convert to 16bit PCM and Write WAV =====
full_wave_int16 = np.int16(full_wave / np.max(np.abs(full_wave)) * 32767)
write("score.wav", fs, full_wave_int16)

# ===== Play =====
Audio("score.wav")


SyntaxError: '[' was never closed (<string>, line 1)

In [ ]:

import ast
import operator as op
import urllib.request

# ===============================
# 安全な式評価（* と + のみ対応）
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Mult: op.mul,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left)
            right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# GitHubからデータ取得
# ===============================
url = "https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1"
with urllib.request.urlopen(url) as r:
    lines = [l.decode("utf-8").strip() for l in r.readlines()]

# ===============================
# 変数定義とスコア行を解析
# ===============================
vars_map = {}
score_lines = []
in_score = False
for i, line in enumerate(lines, 1):
    if not line or line.startswith("#"):
        if "Score" in line:
            in_score = True
        continue
    if not in_score:
        # 変数定義
        if "=" in line:
            try:
                name, val = line.split("=",1)
                name = name.strip()
                val = val.strip()
                vars_map[name] = safe_eval_expr(val, vars_map)
            except Exception as e:
                print(f"[Line {i}] VAR ERROR #: {e}")
    else:
        # スコア行
        parts = [p.strip() for p in line.split(",")]
        if len(parts) < 2:
            continue
        freq_field = parts[1]
        try:
            # リストか単体か判定
            if freq_field.startswith("[") and freq_field.endswith("]"):
                inner = freq_field[1:-1].strip()
                freqs = [safe_eval_expr(x.strip(), vars_map) for x in inner.split(",")]
                print(f"[Line {i}] FREQ OK: {freq_field} => {freqs}")
            else:
                freq = safe_eval_expr(freq_field, vars_map)
                print(f"[Line {i}] FREQ OK: {freq_field} => {freq}")
        except Exception as e:
            print(f"[Line {i}] FREQ ERROR: {freq_field} => {e}")


[Line 9] FREQ OK: f_1*1 => 220
[Line 10] FREQ OK: f_1*2 => 440
[Line 11] FREQ OK: f_1*1 => 220
[Line 12] FREQ OK: f_1*1 => 220
[Line 13] FREQ OK: f_1*2 => 440
[Line 14] FREQ OK: f_1*1 => 220
[Line 15] FREQ OK: f_1*2 => 440
[Line 16] FREQ OK: f_1*2 => 440
[Line 17] FREQ OK: f_1*1 => 220
[Line 18] FREQ OK: f_1*1 => 220
[Line 19] FREQ OK: f_1*2 => 440
[Line 20] FREQ OK: f_1*1 => 220
[Line 21] FREQ OK: f_1*2 => 440
[Line 22] FREQ OK: f_1*1 => 220
[Line 23] FREQ OK: f_1*1 => 220
[Line 24] FREQ OK: f_1*2 => 440
[Line 26] FREQ OK: f_1*1 => 220
[Line 27] FREQ OK: f_1*2 => 440
[Line 28] FREQ OK: f_1*1 => 220
[Line 29] FREQ OK: f_1*1 => 220
[Line 30] FREQ OK: f_1*2 => 440
[Line 31] FREQ OK: f_1*1 => 220
[Line 32] FREQ OK: f_1*2 => 440
[Line 33] FREQ OK: f_1*2 => 440
[Line 34] FREQ OK: f_1*1 => 220
[Line 35] FREQ OK: f_1*1 => 220
[Line 36] FREQ OK: f_1*2 => 440
[Line 37] FREQ OK: f_1*1 => 220
[Line 38] FREQ OK: f_1*2 => 440
[Line 39] FREQ OK: f_1*1 => 220
[Line 40] FREQ OK: f_1*1 => 220
[Line 41]

/tmp/ipython-input-3473979002.py:22: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


In [ ]:
# coding:utf-8
import numpy as np
import requests
from scipy.io.wavfile import write
from IPython.display import Audio

# ===== Load Score from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# Execute code to define variables and score
exec(code, globals())

# Collect all score lines
score_lines = []
for line in code.splitlines():
    line = line.strip()
    if line.startswith("t_") and "," in line:
        line = line.replace('.', 'None')  # 空欄を None に置換
        score_lines.append(line)

# ===== Playback Parameters =====
fs = 44100  # サンプリング周波数

def generate_wave(frequency, duration, wave_type="square"):
    t = np.linspace(0, duration, int(fs*duration), endpoint=False)
    if wave_type == "square":
        return np.sign(np.sin(2*np.pi*frequency*t))
    elif wave_type == "sine":
        return np.sin(2*np.pi*frequency*t)
    elif wave_type == "triangle":
        return 2*np.abs(2*((t*frequency)%1)-1)-1
    elif wave_type == "sawtooth":
        return 2*((t*frequency)%1)-1
    else:
        return np.zeros_like(t)

# ===== Generate Full Wave =====
full_wave = np.array([], dtype=np.float32)

for line in score_lines:
    t_val, f_val, dur_val, wave_val = eval(line)
    duration = dur_val or t_1  # 持続時間が None の場合 t_1 を使用
    wave_type = wave_val or "square"

    # 単音・和音対応
    if isinstance(f_val, list):
        wave = sum(generate_wave(f, duration, wave_type) for f in f_val)
        wave /= len(f_val)  # 正規化
    else:
        wave = generate_wave(f_val, duration, wave_type)

    full_wave = np.concatenate((full_wave, wave))

# 16bit PCM に変換
full_wave_int16 = np.int16(full_wave / np.max(np.abs(full_wave)) * 32767)

# ===== Write WAV =====
write("score.wav", fs, full_wave_int16)

# ===== Play in Colab =====
Audio("score.wav")


SyntaxError: invalid syntax (<string>, line 10)

In [ ]:
# coding:utf-8
import numpy as np
import requests
from scipy.io.wavfile import write
from IPython.display import Audio
import re

# ===== Load Code from GitHub =====
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
code = resp.text

# ===== Execute Variable Definitions Only =====
var_lines = [line for line in code.splitlines() if line.strip().startswith(('t_','f_','ds_','di_','sp_'))]
exec('\n'.join(var_lines), globals())

# ===== Extract Raw Score Lines =====
score_lines_raw = [line.strip() for line in code.splitlines() if re.match(r'^t_\d+\s*\*', line)]

# ===== Fix '.' by replacing with previous values =====
prev = {}  # 前の行の値を保持
score_lines_fixed = []

for line in score_lines_raw:
    parts = [p.strip() for p in line.split(",")]
    fixed_parts = []
    for i, p in enumerate(parts):
        if p == '.':
            fixed_parts.append(prev.get(i))
        else:
            val = eval(p)
            fixed_parts.append(val)
            prev[i] = val
    score_lines_fixed.append(fixed_parts)

# ===== WAV Generation Parameters =====
fs = 44100  # サンプリング周波数

def generate_wave(frequency, duration, wave_type="square"):
    t = np.linspace(0, duration, int(fs*duration), endpoint=False)
    if wave_type == "square":
        return np.sign(np.sin(2*np.pi*frequency*t))
    elif wave_type == "sine":
        return np.sin(2*np.pi*frequency*t)
    elif wave_type == "triangle":
        return 2*np.abs(2*((t*frequency)%1)-1)-1
    elif wave_type == "sawtooth":
        return 2*((t*frequency)%1)-1
    else:
        return np.zeros_like(t)

# ===== Generate Full Wave =====
full_wave = np.array([], dtype=np.float32)

for t_val, f_val, dur_val, wave_val in score_lines_fixed:
    duration = dur_val or t_1  # None の場合は t_1 を使用
    wave_type = wave_val or "square"

    if isinstance(f_val, list):
        wave = sum(generate_wave(f, duration, wave_type) for f in f_val)
        wave /= len(f_val)  # 和音は正規化
    else:
        wave = generate_wave(f_val, duration, wave_type)

    full_wave = np.concatenate((full_wave, wave))

# ===== Convert to 16bit PCM and Write WAV =====
full_wave_int16 = np.int16(full_wave / np.max(np.abs(full_wave)) * 32767)
write("score.wav", fs, full_wave_int16)

# ===== Play in Colab =====
Audio("score.wav")


SyntaxError: invalid syntax (<string>, line 7)

In [ ]:
import ast
import operator as op
import urllib.request

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# GitHubからダウンロード
# ===============================
url = "https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1"
urllib.request.urlretrieve(url, "score.txt")

# ===============================
# デバッグ: 変数と周波数のみ
# ===============================
vars_map = {}
with open("score.txt") as f:
    for i, line in enumerate(f, 1):
        line = line.strip()
        if not line or line.startswith("#"):
            continue
        # 変数定義
        if "=" in line:
            try:
                var_name, var_value = line.split("=", 1)
                var_name = var_name.strip()
                vars_map[var_name] = safe_eval_expr(var_value.strip(), vars_map)
            except Exception as e:
                print(f"[Line {i}] VAR ERROR #: {e}")
            continue
        # スコア解析
        parts = [p.strip() for p in line.split(",")]
        if len(parts) < 2:
            continue
        freq_field = parts[1].strip()
        try:
            # 空白削除して safe_eval
            if freq_field.startswith("[") and freq_field.endswith("]"):
                freq_field_clean = freq_field.replace(" ", "")
            else:
                freq_field_clean = freq_field
            freq_val = safe_eval_expr(freq_field_clean, vars_map)
            print(f"[Line {i}] FREQ OK: {freq_field} => {freq_val}")
        except Exception as e:
            print(f"[Line {i}] FREQ ERROR: {freq_field} => {e}")



[Line 9] FREQ OK: f_1*1 => 220
[Line 10] FREQ OK: f_1*2 => 440
[Line 11] FREQ OK: f_1*1 => 220
[Line 12] FREQ OK: f_1*1 => 220
[Line 13] FREQ OK: f_1*2 => 440
[Line 14] FREQ OK: f_1*1 => 220
[Line 15] FREQ OK: f_1*2 => 440
[Line 16] FREQ OK: f_1*2 => 440
[Line 17] FREQ OK: f_1*1 => 220
[Line 18] FREQ OK: f_1*1 => 220
[Line 19] FREQ OK: f_1*2 => 440
[Line 20] FREQ OK: f_1*1 => 220
[Line 21] FREQ OK: f_1*2 => 440
[Line 22] FREQ OK: f_1*1 => 220
[Line 23] FREQ OK: f_1*1 => 220
[Line 24] FREQ OK: f_1*2 => 440
[Line 26] FREQ OK: f_1*1 => 220
[Line 27] FREQ OK: f_1*2 => 440
[Line 28] FREQ OK: f_1*1 => 220
[Line 29] FREQ OK: f_1*1 => 220
[Line 30] FREQ OK: f_1*2 => 440
[Line 31] FREQ OK: f_1*1 => 220
[Line 32] FREQ OK: f_1*2 => 440
[Line 33] FREQ OK: f_1*2 => 440
[Line 34] FREQ OK: f_1*1 => 220
[Line 35] FREQ OK: f_1*1 => 220
[Line 36] FREQ OK: f_1*2 => 440
[Line 37] FREQ OK: f_1*1 => 220
[Line 38] FREQ OK: f_1*2 => 440
[Line 39] FREQ OK: f_1*1 => 220
[Line 40] FREQ OK: f_1*1 => 220
[Line 41]

/tmp/ipython-input-697838723.py:27: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


In [ ]:
import ast
import operator as op
import requests

# ===============================
# 安全な式評価関数
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left)
            right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# GitHub から楽譜データ取得
# ===============================
url = "https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1"
resp = requests.get(url)
lines = resp.text.splitlines()

# ===============================
# データ変換（変数・スコア分離）
# ===============================
vars_map = {}
score_raw = []
in_score = False

for line in lines:
    line = line.strip()
    if not line or line.startswith("#"):
        if "Score" in line:
            in_score = True
        continue
    if not in_score:
        if "=" in line:
            name, val = line.split("=", 1)
            vars_map[name.strip()] = safe_eval_expr(val.strip(), vars_map)
    else:
        score_raw.append(line)

# ===============================
# スコア読み取り
# ===============================
score = []
prev_start = prev_freq = prev_duration = prev_waveform = None

for raw in score_raw:
    parts = [p.strip() for p in raw.split(",")]
    while len(parts) < 4:  # 足りない項目はドットで補う
        parts.append(".")
    start_field, freq_field, dur_field, wave_field = parts[:4]

    # 開始時間
    start = prev_start if start_field == "." else float(safe_eval_expr(start_field, vars_map))
    # 周波数（単音 or 和音）
    if freq_field == ".":
        freq = prev_freq
    else:
        freq = safe_eval_expr(freq_field, vars_map)
        if isinstance(freq, (list, tuple)):
            freq = [float(f) for f in freq]
        else:
            freq = float(freq)
    # 長さ
    duration = prev_duration if dur_field == "." else float(safe_eval_expr(dur_field, vars_map))
    # 波形
    waveform = prev_waveform if wave_field == "." else wave_field.strip().strip('"').strip("'")

    score.append((start, freq, duration, waveform))
    prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

# ===============================
# デバッグ出力
# ===============================
print("=== Variables ===")
for k, v in vars_map.items():
    print(f"{k} = {v}")
print("\n=== First 10 Score Entries ===")
for s in score[:10]:
    print(s)


/tmp/ipython-input-650351998.py:27: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:
import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    """変数付き式・リスト式を安全に評価"""
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left)
            right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ テキスト楽譜を安全に読み込み（変数・和音対応版）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                # 変数定義行
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # ===== スコア解析 =====
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            if start_field == ".":
                start = prev_start
            else:
                start = float(safe_eval_expr(start_field, vars_map))

            # freq（単音・和音リスト対応）
            if freq_field == ".":
                freq = prev_freq
            else:
                freq_eval = safe_eval_expr(freq_field, vars_map)
                if isinstance(freq_eval, (list, tuple)):
                    freq = [float(x) for x in freq_eval]
                else:
                    freq = float(freq_eval)

            # duration
            if dur_field == ".":
                duration = prev_duration
            else:
                duration = float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                waveform = wave_field.strip().strip('"').strip("'")

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
sr = 44100
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生 & ダウンロード
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")


--2025-09-21 06:51:12--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.3
Connecting to github.com (github.com)|140.82.121.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:51:12--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:51:13 (40.8 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-3191101031.py:29: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:
import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ テキスト楽譜を安全に読み込み（変数・演算・和音対応版）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # ===== スコア解析 =====
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            start = prev_start if start_field == "." else float(safe_eval_expr(start_field, vars_map))

            # freq（単音 or 和音リスト対応）
            if freq_field == ".":
                freq = prev_freq
            else:
                freq = safe_eval_expr(freq_field, vars_map)
                if isinstance(freq, (list, tuple)):
                    freq = [float(x) for x in freq]
                else:
                    freq = float(freq)


            # duration
            duration = prev_duration if dur_field == "." else float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                try:
                    waveform = ast.literal_eval(wave_field)
                    if not isinstance(waveform, str):
                        waveform = str(waveform)
                except Exception:
                    waveform = wave_field.strip().strip('"').strip("'")

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
sr = 44100
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生 & ダウンロード
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")

--2025-09-21 06:46:34--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.3
Connecting to github.com (github.com)|140.82.121.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:46:34--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:46:34 (38.4 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-2624646653.py:28: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:

import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# GitHubからデータを取得
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# デバッグ用：変数と freq_field の評価
# ===============================
vars_map = {}
success_count = 0
fail_count = 0

with open("score.txt") as f:
    for line_no, raw in enumerate(f, 1):
        line = raw.strip()
        if not line or line.startswith("#"):
            # 変数定義行の処理
            if "=" in line:
                var_name, var_value = line.split("=", 1)
                var_name = var_name.strip()
                try:
                    vars_map[var_name] = safe_eval_expr(var_value.strip(), vars_map)
                    print(f"[Line {line_no}] VAR {var_name} = {vars_map[var_name]}")
                except Exception as e:
                    print(f"[Line {line_no}] VAR ERROR {var_name}: {e}")
            continue

        # スコア行かもしれない
        parts = [p.strip() for p in line.split(",")]
        if len(parts) < 2:
            continue
        start_field, freq_field = parts[0], parts[1]

        try:
            # freq_field がリストかどうか
            if freq_field.startswith("[") and freq_field.endswith("]"):
                inner = freq_field[1:-1].split(",")
                freqs = [safe_eval_expr(x.strip(), vars_map) for x in inner]
            else:
                freqs = safe_eval_expr(freq_field, vars_map)
            print(f"[Line {line_no}] FREQ OK: {freqs}")
            success_count += 1
        except Exception as e:
            print(f"[Line {line_no}] FREQ ERROR: {freq_field} => {e}")
            fail_count += 1

print(f"\nTotal: {success_count} success / {fail_count} fail")


--2025-09-21 07:01:30--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.3
Connecting to github.com (github.com)|140.82.121.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 07:01:30--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.108.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 07:01:30 (44.0 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-2317035079.py:26: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


In [ ]:

import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left)
            right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# GitHubから楽譜ダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# スコア解析（変数・和音対応）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                # 変数定義
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # スコア解析
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            start = prev_start if start_field == "." else float(safe_eval_expr(start_field, vars_map))

            # freq（単音 or 和音）
            if freq_field == ".":
                freq = prev_freq
            else:
                freq = safe_eval_expr(freq_field, vars_map)
                if isinstance(freq, (list, tuple)):
                    freq = [float(x) for x in freq]
                else:
                    freq = float(freq)

            # duration
            duration = prev_duration if dur_field == "." else float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                waveform = wave_field.strip().strip('"').strip("'")

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# タイムライン合成
# ===============================
sr = 44100
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 再生 & WAV保存
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")


--2025-09-21 06:36:46--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.3
Connecting to github.com (github.com)|140.82.121.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:36:46--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:36:46 (41.0 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-4041234858.py:28: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:

# ===============================
# 0️⃣ 必要ライブラリ
# ===============================
import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 1️⃣ 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    """変数展開対応・安全な式評価"""
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left)
            right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ スコア解析（変数・和音対応）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                # 変数定義
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # スコア解析
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            start = prev_start if start_field == "." else float(safe_eval_expr(start_field, vars_map))

            # freq (単音 or 和音)
            if freq_field == ".":
                freq = prev_freq
            else:
                try:
                    freq_candidate = ast.literal_eval(freq_field)
                    if isinstance(freq_candidate, (list, tuple)):
                        freq = [float(safe_eval_expr(str(x), vars_map)) for x in freq_candidate]
                    else:
                        freq = float(safe_eval_expr(freq_field, vars_map))
                except:
                    freq = float(safe_eval_expr(freq_field, vars_map))

            # duration
            duration = prev_duration if dur_field == "." else float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                try:
                    waveform = ast.literal_eval(wave_field)
                    if not isinstance(waveform, str):
                        waveform = str(waveform)
                except:
                    waveform = wave_field.strip().strip('"').strip("'")

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
sr = 44100
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生 & WAV保存
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")


--2025-09-21 06:35:22--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.4
Connecting to github.com (github.com)|140.82.121.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:35:22--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:35:22 (41.5 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-1008680978.py:32: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:

import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ テキスト楽譜を安全に読み込み（変数・和音対応版）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                # 変数定義行 (例: t_1 = 0.125)
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # ===== スコア解析 =====
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            if start_field == ".":
                start = prev_start
            else:
                start = float(safe_eval_expr(start_field, vars_map))

            # freq（単音 or 和音リスト対応）
            if freq_field == ".":
                freq = prev_freq
            else:
                freq = safe_eval_expr(freq_field, vars_map)
                if isinstance(freq, (list, tuple)):
                    freq = [float(x) for x in freq]
                else:
                    freq = float(freq)

            # duration
            if dur_field == ".":
                duration = prev_duration
            else:
                duration = float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                try:
                    waveform = ast.literal_eval(wave_field)
                    if not isinstance(waveform, str):
                        waveform = str(waveform)
                except Exception:
                    waveform = wave_field.strip().strip('"').strip("'")

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
sr = 44100  # サンプリング周波数
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生 & ダウンロード
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")


--2025-09-21 06:31:09--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.4
Connecting to github.com (github.com)|140.82.121.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:31:09--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:31:09 (42.0 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-1144113883.py:28: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:


import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ テキスト楽譜を安全に読み込み（変数定義対応版）
# ===============================
def parse_score_file_with_vars(path, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform
    vars_map = {}
    in_score_section = False

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                # スコアセクション開始検出
                if "Score" in line:
                    in_score_section = True
                continue

            if not in_score_section:
                # 変数定義行 (例: t_1 = 0.125)
                if "=" in line:
                    var_name, var_value = line.split("=", 1)
                    var_name = var_name.strip()
                    var_value = safe_eval_expr(var_value.strip(), vars_map)
                    vars_map[var_name] = var_value
                continue

            # ===== スコア解析 =====
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            if start_field == ".":
                start = prev_start
            else:
                start = float(safe_eval_expr(start_field, vars_map))

            # freq
            if freq_field == ".":
                freq = prev_freq
            else:
                try:
                    freq_candidate = ast.literal_eval(freq_field)
                    if isinstance(freq_candidate, (int, float, list, tuple)):
                        freq = freq_candidate
                    else:
                        freq = safe_eval_expr(freq_field, vars_map)
                except Exception:
                    freq = safe_eval_expr(freq_field, vars_map)

            # duration
            if dur_field == ".":
                duration = prev_duration
            else:
                duration = float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                try:
                    waveform = ast.literal_eval(wave_field)
                    if not isinstance(waveform, str):
                        waveform = str(waveform)
                except Exception:
                    waveform = wave_field.strip().strip('"').strip("'")

            # 整形
            if isinstance(freq, (list, tuple)):
                freq = [float(x) for x in freq]
            else:
                freq = float(freq)

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return vars_map, score

vars_map, score = parse_score_file_with_vars("score.txt", default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
sr = 44100  # サンプリング周波数
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生 & ダウンロード
# ===============================
Audio(music, rate=sr)

from scipy.io.wavfile import write
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")


--2025-09-21 06:24:48--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.4
Connecting to github.com (github.com)|140.82.121.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 06:24:48--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3372 (3.3K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   3.29K  --.-KB/s    in 0s      

2025-09-21 06:24:48 (45.4 MB/s) - ‘score.txt’ saved [3372/3372]



/tmp/ipython-input-2009437921.py:28: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


SyntaxError: '[' was never closed (<unknown>, line 1)

In [ ]:



import numpy as np
from IPython.display import Audio
import ast
import operator as op

# ===============================
# 1️⃣ パラメータの定義
# ===============================
t_1 = 0.125
sp_1 = 0
f_1 = 220
f_s = 1
ds_1 = 0.7
di_1 = 0

sr = 44100     # サンプリング周波数

# 評価用変数マップ
vars_map = {
    "t_1": t_1,
    "sp_1": sp_1,
    "f_1": f_1,
    "f_s": f_s,
    "ds_1": ds_1,
    "di_1": di_1,
}

# ===============================
# 安全な式評価
# ===============================
_allowed_ops = {
    ast.Add: op.add,
    ast.Sub: op.sub,
    ast.Mult: op.mul,
    ast.Div: op.truediv,
    ast.Pow: op.pow,
    ast.USub: op.neg,
    ast.UAdd: lambda x: x,
    ast.FloorDiv: op.floordiv,
    ast.Mod: op.mod,
}

def safe_eval_expr(expr: str, names: dict):
    node = ast.parse(expr, mode="eval")
    def _eval(node):
        if isinstance(node, ast.Expression):
            return _eval(node.body)
        if isinstance(node, ast.Constant):
            return node.value
        if isinstance(node, ast.Num):
            return node.n
        if isinstance(node, ast.BinOp):
            left = _eval(node.left); right = _eval(node.right)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](left, right)
            raise ValueError(f"Unsupported op: {op_type}")
        if isinstance(node, ast.UnaryOp):
            operand = _eval(node.operand)
            op_type = type(node.op)
            if op_type in _allowed_ops:
                return _allowed_ops[op_type](operand)
            raise ValueError(f"Unsupported unary op: {op_type}")
        if isinstance(node, ast.Name):
            if node.id in names:
                return names[node.id]
            raise ValueError(f"Unknown name: {node.id}")
        if isinstance(node, (ast.List, ast.Tuple)):
            return [_eval(elt) for elt in node.elts]
        raise ValueError(f"Unsupported AST node: {type(node)}")
    return _eval(node.body)

# ===============================
# 2️⃣ GitHubから楽譜をダウンロード
# ===============================
!wget -O score.txt https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1

# ===============================
# 3️⃣ テキスト楽譜を安全に読み込み
# ===============================
def parse_score_file(path, vars_map, default_waveform="sine"):
    score = []
    prev_start = prev_freq = prev_duration = None
    prev_waveform = default_waveform

    with open(path) as f:
        for raw in f:
            line = raw.strip()
            if not line or line.startswith("#"):
                continue
            parts = [p.strip() for p in line.split(",")]
            while len(parts) < 4:
                parts.append(".")
            start_field, freq_field, dur_field, wave_field = parts[:4]

            # start
            if start_field == ".":
                start = prev_start
            else:
                start = float(safe_eval_expr(start_field, vars_map))

            # freq
            if freq_field == ".":
                freq = prev_freq
            else:
                try:
                    freq_candidate = ast.literal_eval(freq_field)
                    if isinstance(freq_candidate, (int, float, list, tuple)):
                        freq = freq_candidate
                    else:
                        freq = safe_eval_expr(freq_field, vars_map)
                except Exception:
                    freq = safe_eval_expr(freq_field, vars_map)

            # duration
            if dur_field == ".":
                duration = prev_duration
            else:
                duration = float(safe_eval_expr(dur_field, vars_map))

            # waveform
            if wave_field == ".":
                waveform = prev_waveform
            else:
                try:
                    waveform = ast.literal_eval(wave_field)
                    if not isinstance(waveform, str):
                        waveform = str(waveform)
                except Exception:
                    waveform = wave_field.strip().strip('"').strip("'")

            # 整形
            if isinstance(freq, (list, tuple)):
                freq = [float(x) for x in freq]
            else:
                freq = float(freq)

            score.append((start, freq, duration, waveform))
            prev_start, prev_freq, prev_duration, prev_waveform = start, freq, duration, waveform

    return score

score = parse_score_file("score.txt", vars_map, default_waveform="sine")

# ===============================
# 4️⃣ 波形生成関数
# ===============================
def make_wave(freq, duration, waveform="sine"):
    t_arr = np.linspace(0, duration, int(sr*duration), False)
    if freq == 0:
        return np.zeros_like(t_arr)
    if waveform=="sine":
        return np.sin(2*np.pi*freq*t_arr)
    elif waveform=="square":
        return np.sign(np.sin(2*np.pi*freq*t_arr))
    elif waveform=="saw":
        return 2*(t_arr*freq - np.floor(0.5 + t_arr*freq))
    elif waveform=="triangle":
        return 2*np.arcsin(np.sin(2*np.pi*freq*t_arr))/np.pi
    else:
        raise ValueError("unknown waveform")

# ===============================
# 5️⃣ タイムラインに沿って合成
# ===============================
# total_duration をスコア末尾から自動計算
last_time = max((start + duration) for start, _, duration, _ in score)
total_duration = last_time + 0.5  # 末尾に少し余裕
music = np.zeros(int(sr * total_duration))

for start, f, duration, waveform in score:
    if isinstance(f, list):
        wave = sum(make_wave(fi, duration, waveform) for fi in f) / len(f)
    else:
        wave = make_wave(f, duration, waveform)
    start_i = int(start * sr)
    end_i = min(start_i + len(wave), len(music))
    music[start_i:end_i] += wave[:end_i-start_i]

# 正規化
music = music / np.max(np.abs(music))

# ===============================
# 6️⃣ 再生
# ===============================
Audio(music, rate=sr)


--2025-09-21 04:26:43--  https://github.com/the-fur-lover-sketch/effective-invention/raw/refs/heads/main/Sheet1
Resolving github.com (github.com)... 140.82.121.3
Connecting to github.com (github.com)|140.82.121.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1 [following]
--2025-09-21 04:26:43--  https://raw.githubusercontent.com/the-fur-lover-sketch/effective-invention/refs/heads/main/Sheet1
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2953 (2.9K) [text/plain]
Saving to: ‘score.txt’

score.txt           100%[===================>]   2.88K  --.-KB/s    in 0s      

2025-09-21 04:26:44 (38.0 MB/s) - ‘score.txt’ saved [2953/2953]



/tmp/ipython-input-446859637.py:50: DeprecationWarning: ast.Num is deprecated and will be removed in Python 3.14; use ast.Constant instead
  if isinstance(node, ast.Num):


In [ ]:


from scipy.io.wavfile import write

# 音声データを16bit PCMに変換
write("music.wav", sr, (music * 32767).astype(np.int16))

from google.colab import files
files.download("music.wav")




<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>